# 0. *Импорт библиотек и вспомогательные функции/классы*

In [2]:
!pip install optuna

In [4]:
import optuna
import sklearn.ensemble
import sklearn.svm
import logging

In [5]:
import logging
import sys

import sklearn.datasets
import sklearn.linear_model
import sklearn.model_selection
import optuna

In [6]:
from optuna.visualization import plot_contour
from optuna.visualization import plot_edf
from optuna.visualization import plot_intermediate_values
from optuna.visualization import plot_optimization_history
from optuna.visualization import plot_parallel_coordinate
from optuna.visualization import plot_param_importances
from optuna.visualization import plot_slice

# 1. *Применение оптуны на функцию Матьяса*

In [7]:
def f_mat (x, y):
  return 0.26*(x*x +y*y)-0.48*x*y

def objective(trial):
  x = trial.suggest_float('x', -10, 10)
  y = trial.suggest_float('y', -10, 10)
  return f_mat (x, y)

In [8]:
optuna.logging.disable_default_handler() 
optuna.logging.disable_propagation()
study =optuna.create_study()
study.optimize(objective, n_trials=100)


In [9]:
best_params = study.best_params
found_x = best_params['x']
found_y = best_params['y']
print(f"Found x: {found_x},  Found y: {found_y}, f_mat(x,y): {f_mat(found_x, found_y)}")

Found x: 0.16420917625759057,  Found y: 0.18880464284679643, f_mat(x,y): 0.0013974218089718368


# 2. *Использование datasets Iris и оптимизация параметров с помощью optuna*

In [10]:
def objective(trial):
    iris = sklearn.datasets.load_iris()  # грузим датасет
    classes = list(set(iris.target))
    train_x, valid_x, train_y, valid_y = sklearn.model_selection.train_test_split( # разюитие на тест и тренировку в данном случае 75 на 25
        iris.data, iris.target, test_size=0.25, random_state=0
    )


    max_iter = trial.suggest_int("max_iter", 50, 400)
    verbose = trial.suggest_int("verbose", 0, 100)
    clf = sklearn.linear_model.SGDClassifier(max_iter=max_iter, verbose = verbose)

    for step in range(100):
        clf.fit(train_x, train_y)

        # Report intermediate objective value.
        intermediate_value = 1.0 - clf.score(valid_x, valid_y)
        trial.report(intermediate_value, step)

        # Handle pruning based on the intermediate value.
        if trial.should_prune():
            raise optuna.TrialPruned()

    return 1.0 - clf.score(valid_x, valid_y)


In [11]:
optuna.logging.disable_default_handler() 
optuna.logging.disable_propagation()
optuna.logging.get_logger("optuna").addHandler(logging.StreamHandler(sys.stdout))
study = optuna.create_study(pruner=optuna.pruners.MedianPruner())
study.optimize(objective, n_trials=20)

A new study created in memory with name: no-name-56358c55-150b-4fd2-a671-1f96980ddfff
-- Epoch 1
Norm: 27.39, NNZs: 4, Bias: -0.019960, T: 112, Avg. loss: 3.634865
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 24.88, NNZs: 4, Bias: -0.019960, T: 224, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 22.79, NNZs: 4, Bias: -0.019960, T: 336, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 21.03, NNZs: 4, Bias: -0.019960, T: 448, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 5
Norm: 19.52, NNZs: 4, Bias: -0.019960, T: 560, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 6
Norm: 18.21, NNZs: 4, Bias: -0.019960, T: 672, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 7
Norm: 17.07, NNZs: 4, Bias: -0.019960, T: 784, Avg. loss: 0.000000
Total training time: 0.00 seconds.
Convergence after 7 epochs took 0.00 seconds
-- Epoch 1
Norm: 78.27, NNZs: 4, Bias: 8.425789, T: 112, Avg. loss: 152.487366

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0

-- Epoch 1
Norm: 87.02, NNZs: 4, Bias: 9.931301, T: 112, Avg. loss: 12.233153
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 79.05, NNZs: 4, Bias: 9.931301, T: 224, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 72.42, NNZs: 4, Bias: 9.931301, T: 336, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 66.81, NNZs: 4, Bias: 9.931301, T: 448, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 5
Norm: 62.01, NNZs: 4, Bias: 9.931301, T: 560, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 6
Norm: 57.86, NNZs: 4, Bias: 9.931301, T: 672, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 7
Norm: 54.22, NNZs: 4, Bias: 9.931301, T: 784, Avg. loss: 0.000000
Total training time: 0.00 seconds.
Convergence after 7 epochs took 0.00 seconds
-- Epoch 1
Norm: 108.57, NNZs: 4, Bias: 0.021953, T: 112, Avg. loss: 134.005755
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 121.05, NNZs: 4, Bias: 8.805811, T: 22

[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.

Norm: 161.60, NNZs: 4, Bias: 126.424205, T: 2576, Avg. loss: 27.980418
Total training time: 0.00 seconds.
-- Epoch 24
Norm: 154.98, NNZs: 4, Bias: 129.237412, T: 2688, Avg. loss: 29.292079
Total training time: 0.00 seconds.
-- Epoch 25
Norm: 152.49, NNZs: 4, Bias: 134.576531, T: 2800, Avg. loss: 38.536957
Total training time: 0.00 seconds.
-- Epoch 26
Norm: 156.57, NNZs: 4, Bias: 131.915254, T: 2912, Avg. loss: 18.472373
Total training time: 0.00 seconds.
-- Epoch 27
Norm: 156.15, NNZs: 4, Bias: 134.420863, T: 3024, Avg. loss: 30.924065
Total training time: 0.00 seconds.
-- Epoch 28
Norm: 155.20, NNZs: 4, Bias: 134.416346, T: 3136, Avg. loss: 30.501692
Total training time: 0.00 seconds.
-- Epoch 29
Norm: 149.04, NNZs: 4, Bias: 136.852149, T: 3248, Avg. loss: 25.980331
Total training time: 0.00 seconds.
-- Epoch 30
Norm: 144.85, NNZs: 4, Bias: 139.162659, T: 3360, Avg. loss: 27.111426
Total training time: 0.00 seconds.
-- Epoch 31
Norm: 144.22, NNZs: 4, Bias: 141.417367, T: 3472, Avg. l

...

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0

-- Epoch 1
Norm: 112.36, NNZs: 4, Bias: 9.755317, T: 112, Avg. loss: 12.004617
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 102.07, NNZs: 4, Bias: 9.755317, T: 224, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 93.50, NNZs: 4, Bias: 9.755317, T: 336, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 86.27, NNZs: 4, Bias: 9.755317, T: 448, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 5
Norm: 80.07, NNZs: 4, Bias: 9.755317, T: 560, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 6
Norm: 74.70, NNZs: 4, Bias: 9.755317, T: 672, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 7
Norm: 70.01, NNZs: 4, Bias: 9.755317, T: 784, Avg. loss: 0.000000
Total training time: 0.00 seconds.
Convergence after 7 epochs took 0.00 seconds
-- Epoch 1
Norm: 112.91, NNZs: 4, Bias: -0.401591, T: 112, Avg. loss: 137.721353
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 115.10, NNZs: 4, Bias: 17.295011, T

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.

Norm: 73.52, NNZs: 4, Bias: 9.842125, T: 336, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 67.83, NNZs: 4, Bias: 9.842125, T: 448, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 5
Norm: 62.96, NNZs: 4, Bias: 9.842125, T: 560, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 6
Norm: 58.74, NNZs: 4, Bias: 9.842125, T: 672, Avg. loss: 0.000000
Total training time: 0.00 seconds.
-- Epoch 7
Norm: 55.05, NNZs: 4, Bias: 9.842125, T: 784, Avg. loss: 0.000000
Total training time: 0.00 seconds.
Convergence after 7 epochs took 0.00 seconds
-- Epoch 1
Norm: 84.92, NNZs: 4, Bias: -0.003690, T: 112, Avg. loss: 145.490962
Total training time: 0.00 seconds.
-- Epoch 2
Norm: 139.43, NNZs: 4, Bias: 0.501117, T: 224, Avg. loss: 112.749856
Total training time: 0.00 seconds.
-- Epoch 3
Norm: 155.34, NNZs: 4, Bias: 16.542054, T: 336, Avg. loss: 112.706433
Total training time: 0.00 seconds.
-- Epoch 4
Norm: 171.31, NNZs: 4, Bias: 24.016939, T: 448, A

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished
[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   2 out of   2 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s remaining:    0.0s
[Parallel(n_jobs=1)]: Done   3 out of   3 | elapsed:    0.0s finished


In [12]:
plot_optimization_history(study)


In [13]:

plot_contour(study)


In [14]:
plot_parallel_coordinate(study)


In [15]:
plot_slice(study)


In [16]:
plot_param_importances(study)


In [17]:
plot_edf(study)